<h1>Lab4

In [1]:
#import libraries
import numpy as np
import pandas as pd
import seaborn as sb
import networkx as nx
import matplotlib.pyplot as plt

In [2]:
filename = "SFlow_Data_lab4.csv"

In [3]:
lab4DF = pd.read_csv(filename, header=None)
dataDF = lab4DF[lab4DF[0] == 'FLOW'] #to remove CNTR entries

print("Lab4 data shape: " + str(lab4DF.shape))
print("Flow entries data shape: " + str(dataDF.shape))

Lab4 data shape: (69370, 21)
Flow entries data shape: (68065, 21)


In [4]:
#Add column headers according to Table 1
dataDF.columns = ["Type","sflow_agent_address","inputPort","outputPort",
                 "src_MAC","dst_MAC","ethernet_type","in_vlan","out_vlan",
                  "src_IP","dst_IP","IP_protocol","ip_tos","ip_ttl",
                  "src_port","dst_port","tcp_flags","packet_size",
                  "IP_size","sampling_rate","Untitled"]

<h2>Exercise 4A

Top 5 Talkers

In [5]:
srcIP_DF = dataDF.src_IP.value_counts()
srcIP_DF.head(5)

193.62.192.8     3041
155.69.160.32    2975
130.14.250.11    2604
14.139.196.58    2452
140.112.8.139    2056
Name: src_IP, dtype: int64

Top 5 Listeners

In [6]:
dst_IP_DF = dataDF.dst_IP.value_counts()
dst_IP_DF.head(5)

103.37.198.100     3841
137.132.228.15     3715
202.21.159.244     2446
192.101.107.153    2368
103.21.126.2       2056
Name: dst_IP, dtype: int64

<h2>Exercise 4B

Percentage of TCP and UDP

In [7]:
#TCP = 6, UDP = 17
tcpDF = dataDF[dataDF.IP_protocol == 6]
tcp_count = tcpDF.shape[0]
udpDF = dataDF[dataDF.IP_protocol == 17]
udp_count = udpDF.shape[0]

total_traffic = dataDF.shape[0]

print("Number of TCP traffic: " + str(tcp_count))
print("Number of UDP traffic: " + str(udp_count))
print()
print(f'Percentage of TCP traffic: {tcp_count/total_traffic*100:.2f}%')
print(f'Percentage of UDP traffic: {udp_count/total_traffic*100:.2f}%')

Number of TCP traffic: 56064
Number of UDP traffic: 9462

Percentage of TCP traffic: 82.37%
Percentage of UDP traffic: 13.90%


Top 3 protocol types: # of packets

In [8]:
IP_protocol_DF = pd.DataFrame(dataDF.IP_protocol.value_counts())
total_traffic = IP_protocol_DF.IP_protocol.sum()
IP_protocol_DF["# of packets"] = (IP_protocol_DF[IP_protocol_DF.columns[0]])
IP_protocol_DF.sort_values(by = '# of packets',ascending=False).head(3)

IP_protocol  # of packets
6         56064         56064
17         9462          9462
50         1698          1698

<h2>Exercise 4C

Top 5 Applications

In [9]:
appDF = dataDF.dst_port.value_counts()
appDF.head(5)

443      13423
80        2647
52866     2068
45512     1356
56152     1341
Name: dst_port, dtype: int64

Port 443 is most frequently used, which means most traffic are passed on secured HTTP

<h2>Exercise 4D

Traffic Intensity (Assume sampling rate is 1 in 1000)

In [10]:
sampling_rate = 1000

total_traffic = dataDF.packet_size.sum()*sampling_rate
#Assuming that unit is bytes, converting to MB
total_traffic_MB = total_traffic/1024/1024
print(f'Total network traffic: {total_traffic_MB:.2f}MB')

#Calculate the same for IP bytes
IP_traffic = dataDF.IP_size.sum()*sampling_rate
IP_traffic_MB = IP_traffic/1024/1024 
print(f'IP traffic: {IP_traffic_MB:.2f}MB')

MAC_traffic_MB = total_traffic_MB - IP_traffic_MB
MAC_traffic_percentage = MAC_traffic_MB/total_traffic_MB*100
print(f'Percentage of MAC header in total network traffic: {MAC_traffic_percentage:.2f}%')

Total network traffic: 63133.70MB
IP traffic: 61776.95MB
Percentage of MAC header in total network traffic: 2.15%


Determine if there is congestion: compare traffic to bandwidth

<h2> Exercise 4E

Top 5 Communication Pairs

In [11]:
IP_pairs = dataDF.groupby(['src_IP','dst_IP']).count()
IP_pairs_DF = pd.DataFrame(IP_pairs.Type)
IP_pairs_DF = IP_pairs_DF.sort_values(by = 'Type',ascending=False)
IP_pairs_DF.columns = ["Count"]
IP_pairs_DF.head(5)

Count
src_IP         dst_IP                
193.62.192.8   137.132.228.15    3041
130.14.250.11  103.37.198.100    2599
14.139.196.58  192.101.107.153   2368
140.112.8.139  103.21.126.2      2056
137.132.228.15 193.62.192.8      1910

Visualisation of communications between different IP hosts

In [12]:
IP_pairs_list = list(IP_pairs_DF.index)

graph = nx.Graph()
for onepair in IP_pairs_list:
    graph.add_edge(onepair[0], onepair[1])

In [13]:
import warnings
warnings.filterwarnings("ignore")

plt.figure(2, figsize=(100,100))
nx.draw(graph, with_labels=True, font_size=10)
plt.show()